# Example of preprocessing of reference data

In this notebook you can find an example of how a spatial dataset with data on cycling infrastructure can be converted to the format needed by the data quality analysis workflow.

The preprocessing must be adapted to the the content and format of your own data.

As stated in the **README**, the reference data should:

- only contain **cycling infrastructure** (i.e. not also the regular street network)
- have all geometries as **LineStrings** (not MultiLineString)
- for each row, the geometry should be a **straight** LineString only defined by its start- and end nodes
- have start/end nodes at **intersections**
- be in a **CRS** recognised by GeoPandas
- contain a column describing whether each feature is a physically **protected**/separated infrastructure or if it is **unprotected**
- contain a column describing whether each feture is **bidirectional** or not (see README for details)
- contain a column describing how features have been **digitized** ('geometry type') (see README for details)
- contain a column with a unique **ID** for each feature

## Bicycle infrastructure data from the City of Copenhagen

The data used in this notebook is from the City of Copenhagen and was downloaded from [opendata.dk](https://www.opendata.dk/city-of-copenhagen/cykeldata) under the [Open Data DK license](https://www.opendata.dk/open-data-dk/open-data-dk-licens).

In [2]:
import folium
import geopandas as gpd
import matplotlib.pyplot as plt
import momepy
from shapely.ops import linemerge

from src import plotting_functions as pf

folium_layers = {
    "Google Satellite": folium.TileLayer(
        tiles="https://mt1.google.com/vt/lyrs=s&x={x}&y={y}&z={z}",
        attr="Google",
        name="Google Satellite",
        overlay=True,
        control=True,
        show=False,
    ),
    "whiteback": folium.TileLayer(
        tiles="https://api.mapbox.com/styles/v1/krktalilu/ckrdjkf0r2jt217qyoai4ndws/tiles/256/{z}/{x}/{y}@2x?access_token=pk.eyJ1Ijoia3JrdGFsaWx1IiwiYSI6ImNrcmRqMXdycTB3NG8yb3BlcGpiM2JkczUifQ.gEfOn5ttzfH5BQTjqXMs3w",
        name="Background: White",
        attr="Mapbox",
        control=True,
        overlay=True,
        show=False,
    ),
    "Stamen TonerLite": folium.TileLayer(
        tiles="https://stamen-tiles-{s}.a.ssl.fastly.net/toner-lite/{z}/{x}/{y}{r}.png",
        attr='Map tiles by <a href="http://stamen.com">Stamen Design</a>, <a href="http://creativecommons.org/licenses/by/3.0">CC BY 3.0</a> &mdash; Map data &copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors',
        name="Stamen TonerLite",
        control=True,
        overlay=True,
        show=False,
    ),
    "CyclOSM": folium.TileLayer(
        tiles="https://{s}.tile-cyclosm.openstreetmap.fr/cyclosm/{z}/{x}/{y}.png",
        attr='Map data &copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors',
        name="CyclOSM",
        control=True,
        overlay=True,
        show=False,
    ),
    "OSM": folium.TileLayer(
        tiles="openstreetmap",
        name="OpenStreetMap",
        attr='Map data &copy; <a href="https://www.openstreetmap.org/copyright">OpenStreetMap</a> contributors',
        control=True,
        overlay=True,
    ),
}

In [3]:
kk = gpd.GeoDataFrame.from_file(
    "../data/ex1_cph_municipality/cykeldata_kk/cykeldata_kk.shp"
)

kk.sample(10)

id rute_nr       rutenavn        status       kategori under_kate  \
1935  1274    None           None  Eksisterende       Cykelsti       None   
2256  1706    None           None  Eksisterende       Cykelsti          P   
3195  4845     C75  Roskilderuten   Projekteret  Supercykelsti       None   
811   2105    None           None  Eksisterende       Cykelsti          P   
2555  2151    None           None  Eksisterende       Cykelsti          P   
2489  2070    None           None  Eksisterende       Cykelsti       None   
2606  2286    None           None  Eksisterende       Cykelsti       None   
3135   219      16        Søruten      Planlagt           Grøn       None   
339    667    None           None  Eksisterende  Cykelmulighed       None   
3272  5211     C85    Tårnbyruten      Planlagt  Supercykelsti       None   

        kommune                                           geometry  
1935  København  LINESTRING (12.46799 55.71245, 12.46797 55.712...  
2256  København  LINESTRING (12.60418 55.66829, 12.60446 55.668...  
3195  København  MULTILINESTRING ((12.56788 55.67575, 12.56254 ...  
811   København  LINESTRING (12.55531 55.69999, 12.55567 55.700...  
2555  København  LINESTRING (12.58890 55.65493, 12.58956 55.654...  
2489  København  LINESTRING (12.57682 55.69457, 12.57687 55.694...  
2606  København  LINESTRING (12.54895 55.70360, 12.54920 55.70374)  
3135  København  LINESTRING (12.55577 55.66806, 12.55592 55.667...  
339   København  LINESTRING (12.56825 55.66112, 12.56765 55.660...  
3272  København  MULTILINESTRING ((12.58816 55.69143, 12.58836 ...

Our dataset both contains physical infrastructure and bicycle routes etc. We are only interested in the physical infrastructure and thus need to select a subset of the data.

Some of the data might be outside of the study area we are interested in, but the data processing in notebook 01 will clip all data to the desired extent.

In [4]:
# Creating subset only with existing cycling infrastructure
kk_selection = kk.loc[
    (kk.kategori == "Cykelsti") & (kk.status == "Eksisterende")
].copy()

kk_selection.explore()

For all code to run without errors, our dataset can only contain LineString geometries. Let's check what we have:

In [5]:
kk_selection.geom_type.unique()

array(['LineString', 'MultiLineString'], dtype=object)

We both have LineStrings and MultiLineStrings here. To fix this, we first try to merge the MultiLineStrings. 
If some of the MultiLinestrings are not connected (i.e. there are gaps in the lines), the aboves step will not be able to merge them. In that case we can instead 'explode' them.

In [6]:
kk_linestrings = kk_selection.copy()
# Convert MultiLineStrings to LineString
kk_linestrings["geometry"] = kk_linestrings["geometry"].apply(
    lambda x: linemerge(x) if x.geom_type == "MultiLineString" else x
)

if (
    len(kk_linestrings.geom_type.unique()) > 1
    or kk_linestrings.geom_type.unique()[0] != "LineString"
):

    print("Exploding MultiLineStrings...")
    kk_linestrings = kk_selection.explode(ignore_index=True)

assert len(kk_linestrings.geom_type.unique()) == 1
assert kk_linestrings.geom_type.unique()[0] == "LineString"
kk_linestrings.geom_type.unique()

array(['LineString'], dtype=object)

For the code to work, the data need to be in a CRS recognized by GeoPandas, and to have that CRS defined. Let's check that we have a CRS defined:

In [7]:
kk_linestrings.crs

<Geographic 2D CRS: GEOGCS["WGS 84",DATUM["WGS_1984",SPHEROID["WGS 84" ...>
Name: WGS 84
Axis Info [ellipsoidal]:
- lon[east]: Longitude (degree)
- lat[north]: Latitude (degree)
Area of Use:
- undefined
Datum: World Geodetic System 1984
- Ellipsoid: WGS 84
- Prime Meridian: Greenwich

The analysis of data quality is based on the concept of a *network*. For the results to be accurate we need a dataset with nodes at intersections (i.e. where the lines defining the cycling infrastructure intersect).

Use the folium plot below to check that you do have nodes at intersections.
If not, this will have to be fixed - or it will be an aspect of low data quality that will become apparent in the analysis of data quality...

Don't worry if there are more nodes than just those at intersections and start/end points - we will take care of that in the data loading notebook.

In [8]:
G = momepy.gdf_to_nx(
    kk_linestrings.to_crs("EPSG:25832"), approach="primal", directed=True
)  # We reproject the network data to avoid warnings - final reprojection will happen later

nodes, edges = momepy.nx_to_gdf(G)

# Feature groups for OSM
edges_folium = pf.make_edgefeaturegroup(
    gdf=edges, mycolor="black", myweight=2, nametag="edges", show_edges=True
)

nodes_folim = pf.make_nodefeaturegroup(
    gdf=nodes, mycolor="red", mysize=2, nametag="nodes", show_nodes=True
)

feature_groups = [edges_folium, nodes_folim]

m = pf.make_foliumplot(
    feature_groups=feature_groups,
    layers_dict=folium_layers,
    center_gdf=nodes,
    center_crs=nodes.crs,
)

display(m)

We don't technically need to drop any unnecessary columns, but let's avoid loading unnecessary data later on.

In [9]:
kk_linestrings.columns

Index(['id', 'rute_nr', 'rutenavn', 'status', 'kategori', 'under_kate',
       'kommune', 'geometry'],
      dtype='object')

In [10]:
# Drop unnecessary columns
kk_linestrings.drop(
    ["rute_nr", "rutenavn", "under_kate", "kommune", "status"], axis=1, inplace=True
)

For this dataset we assume of all features to be center line mappings and bidirectional, so we can specify this in config file and do not have to add it to the data.

The rest of the pre-processing, such as projecting to the chosen CRS, clipping the data to the study area etc. will happen in the [01 load data notebook](../scripts/01_load_data.ipynb).

**Final dataset**

In [11]:
kk_linestrings.sample(10)

id  kategori                                           geometry
996   2698  Cykelsti  LINESTRING (12.54831 55.67224, 12.54798 55.672...
910   2254  Cykelsti  LINESTRING (12.57754 55.71293, 12.57753 55.713...
1187  2966  Cykelsti  LINESTRING (12.48998 55.70597, 12.48979 55.706...
1845  1143  Cykelsti  LINESTRING (12.48187 55.68877, 12.48162 55.689...
598   4055  Cykelsti  LINESTRING (12.59347 55.70871, 12.59409 55.708...
1801  1076  Cykelsti  LINESTRING (12.48636 55.65510, 12.48625 55.655...
2171  1635  Cykelsti  LINESTRING (12.60381 55.65776, 12.60400 55.657...
721   1949  Cykelsti  LINESTRING (12.57737 55.71662, 12.57761 55.716...
2264  1707  Cykelsti  LINESTRING (12.60666 55.66809, 12.60667 55.668...
668   1333  Cykelsti  LINESTRING (12.48202 55.67267, 12.48029 55.672...

*Export dataset*

In [12]:
kk.to_file("../data/ex1_cph_municipality/cph_cycling_infra.gpkg", driver="GPKG")

/opt/miniconda3/envs/cdq/lib/python3.10/site-packages/geopandas/io/file.py:362: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  pd.Int64Index,


Data: © Københavns Kommune